
# 基于模型和顺序特征选择

此示例说明并比较了两种特征选择方法：
基于特征重要性的 :class:`~sklearn.feature_selection.SelectFromModel` 和
依赖于贪婪方法的 :class:`~sklearn.feature_selection.SequentialFeatureSelector` 。

我们使用糖尿病数据集，该数据集包含从442名糖尿病患者收集的10个特征。

作者:[Manoj Kumar](mks542@nyu.edu)  ,
 [Maria Telenczuk](https://github.com/maikia)  , Nicolas Hug.

许可证: BSD 3条款


## 加载数据

我们首先加载scikit-learn中提供的糖尿病数据集，并打印其描述：



In [ ]:
from sklearn.datasets import load_diabetes

diabetes = load_diabetes()
X, y = diabetes.data, diabetes.target
print(diabetes.DESCR)

## 从系数中提取特征重要性

为了了解特征的重要性，我们将使用 :class:`~sklearn.linear_model.RidgeCV` 估计器。具有最高绝对 `coef_` 值的特征被认为是最重要的。我们可以直接观察系数，而不需要对它们（或数据）进行缩放，因为从上面的描述中，我们知道这些特征已经标准化。关于线性模型系数解释的更完整示例，可以参考 `sphx_glr_auto_examples_inspection_plot_linear_model_coefficient_interpretation.py` 。



In [ ]:
import matplotlib.pyplot as plt
import numpy as np

from sklearn.linear_model import RidgeCV

ridge = RidgeCV(alphas=np.logspace(-6, 6, num=5)).fit(X, y)
importance = np.abs(ridge.coef_)
feature_names = np.array(diabetes.feature_names)
plt.bar(height=importance, x=feature_names)
plt.title("Feature importances via coefficients")
plt.show()

## 根据重要性选择特征

现在我们希望根据系数选择两个最重要的特征。:class:`~sklearn.feature_selection.SelectFromModel` 就是为此目的设计的。:class:`~sklearn.feature_selection.SelectFromModel` 接受一个 `threshold` 参数，并将选择重要性（由系数定义）高于此阈值的特征。

由于我们只想选择两个特征，因此我们将阈值设置得略高于第三重要特征的系数。



In [ ]:
from time import time

from sklearn.feature_selection import SelectFromModel

threshold = np.sort(importance)[-3] + 0.01

tic = time()
sfm = SelectFromModel(ridge, threshold=threshold).fit(X, y)
toc = time()
print(f"Features selected by SelectFromModel: {feature_names[sfm.get_support()]}")
print(f"Done in {toc - tic:.3f}s")

## 使用顺序特征选择进行特征选择

另一种选择特征的方法是使用 :class:`~sklearn.feature_selection.SequentialFeatureSelector` (SFS)。SFS 是一种贪婪的过程，在每次迭代中，我们根据交叉验证得分选择要添加到已选特征中的最佳新特征。也就是说，我们从 0 个特征开始，选择得分最高的最佳单一特征。该过程重复进行，直到我们达到所需的选定特征数量。

我们也可以反向进行（向后序列特征选择，backward SFS），即从所有特征开始，逐个贪婪地选择要移除的特征。我们在这里展示这两种方法。



In [ ]:
from sklearn.feature_selection import SequentialFeatureSelector

tic_fwd = time()
sfs_forward = SequentialFeatureSelector(
    ridge, n_features_to_select=2, direction="forward"
).fit(X, y)
toc_fwd = time()

tic_bwd = time()
sfs_backward = SequentialFeatureSelector(
    ridge, n_features_to_select=2, direction="backward"
).fit(X, y)
toc_bwd = time()

print(
    "Features selected by forward sequential selection: "
    f"{feature_names[sfs_forward.get_support()]}"
)
print(f"Done in {toc_fwd - tic_fwd:.3f}s")
print(
    "Features selected by backward sequential selection: "
    f"{feature_names[sfs_backward.get_support()]}"
)
print(f"Done in {toc_bwd - tic_bwd:.3f}s")

有趣的是，前向选择和后向选择选择了相同的特征集。通常情况下，情况并非如此，这两种方法会导致不同的结果。

我们还注意到，SFS选择的特征与特征重要性选择的特征不同：SFS选择了 `bmi` 而不是 `s1` 。不过这听起来是合理的，因为根据系数， `bmi` 是第三重要的特征。考虑到SFS完全不使用系数，这一点相当显著。

最后，我们应该注意到 :class:`~sklearn.feature_selection.SelectFromModel` 比 SFS 快得多。实际上，:class:`~sklearn.feature_selection.SelectFromModel` 只需要拟合一次模型，而 SFS 需要在每次迭代中交叉验证许多不同的模型。然而，SFS 可以与任何模型一起使用，而 :class:`~sklearn.feature_selection.SelectFromModel` 要求底层估计器具有 `coef_` 属性或 `feature_importances_` 属性。前向 SFS 比后向 SFS 快，因为它只需要执行 `n_features_to_select = 2` 次迭代，而后向 SFS 需要执行 `n_features - n_features_to_select = 8` 次迭代。

## 使用负容差值

:class:`~sklearn.feature_selection.SequentialFeatureSelector` 可以用于移除数据集中存在的特征，并返回一个较小的原始特征子集，使用 `direction="backward"` 和负值的 `tol` 。

我们首先加载乳腺癌数据集，该数据集包含30个不同的特征和569个样本。



In [ ]:
import numpy as np

from sklearn.datasets import load_breast_cancer

breast_cancer_data = load_breast_cancer()
X, y = breast_cancer_data.data, breast_cancer_data.target
feature_names = np.array(breast_cancer_data.feature_names)
print(breast_cancer_data.DESCR)

我们将使用 :class:`~sklearn.linear_model.LogisticRegression` 估计器与 :class:`~sklearn.feature_selection.SequentialFeatureSelector` 进行特征选择。



In [ ]:
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_auc_score
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import StandardScaler

for tol in [-1e-2, -1e-3, -1e-4]:
    start = time()
    feature_selector = SequentialFeatureSelector(
        LogisticRegression(),
        n_features_to_select="auto",
        direction="backward",
        scoring="roc_auc",
        tol=tol,
        n_jobs=2,
    )
    model = make_pipeline(StandardScaler(), feature_selector, LogisticRegression())
    model.fit(X, y)
    end = time()
    print(f"\ntol: {tol}")
    print(f"Features selected: {feature_names[model[1].get_support()]}")
    print(f"ROC AUC score: {roc_auc_score(y, model.predict_proba(X)[:, 1]):.3f}")
    print(f"Done in {end - start:.3f}s")

我们可以看到，随着 `tol` 的负值接近零，选择的特征数量趋于增加。特征选择所花费的时间也随着 `tol` 值接近零而减少。

